# Juego de la Vida (Game of Life)

El **Juego de la Vida**, también conocido como **Vida**, es un autómata celular diseñador por el matemático británico John Horton Conway en 1970. Es un juego sin jugadores, esto significa que su evolución está determinada por su estado inicial, sin requerir más entradas. Uno interactúa con el Juego de la Vida al crear un estado inicial (o configuración inicial) y se observa como evoluciona. Es Turing completo (puede simular cualquier máquina de Turing) y puede simular un constructor universal o cualquier otra máquina de Turing.

<center>
<img src="https://1.bp.blogspot.com/-pdQ2ckeQzCw/WwGFbYTKRoI/AAAAAAAAAY8/kb-gcutnkKc2TnQainAlYK5FlWmv87XywCPcBGAYYCw/s1600/ezgif.com-video-to-gif.gif" width=250 height=250 />
</center>

## Reglas

El universo (o entorno) del Juego de la Vida es infinito, cuadrícula ortogonal bidimensional de celdas cuadradas, cada una de ellas se encuentra con uno de dos posibles estados, vivo o muerto (o poblado o despoblado, respectivamente). Cada celda interactúa con ocho vecinos, que son las celdas adyacentes horizontales, verticales y diagonales. En cada paso de tiempo, las siguientes transiciones ocurren:

1. Cualquier celda viva con menos de dos vecinos vivos muere, debido a la poca población.
2. Cualquier celda viva con dos o tres vecinos vivos sobrevive para la siguiente generación.
3. Cualquier celda con más de tres vecinos vivos muere, debido a sobre población.
4. Cualquier celda muerta con exactamente tres vecinos vivos se convierte en una celda viva, debido a la reproducción.

Estas reglas, que comparan el comportamiento del autómata a la vida real, pueden ser condensadas en lo siguiente:

1. Cualquier celda viva con dos o más vecinos vivos sobrevive.
2. Cualquier celda muerta con tres vecinos vivos se convierte en una celda viva.
3. Cualquier otra celda viva muere en la siguiente generación. De manera similar, cualquier otra celda muerta se queda muerta.

El patrón inicial constituye la semilla del sistema. La primera generación es creada al aplicar las reglas anteriores de manera simultanea a cualquier celda en la semilla, viva o muerta; nacimientos y muertes ocurren simultáneamente, y el momento discreto en el cual esto pasa es a veces llamado turno. Cada generación es una función pura de la anterior. Las reglas se aplican de forma repetida para crear nuevas generaciones.

## Imports

Antes de empezar a crear el modelo del juego de la vida con multiagentes es necesario tener instalado los siguientes paquetes:
- `python`: asegúrense de usar la versión 3+.
- `mesa`: el framework de Python para el modelado de agentes.
- `numpy`: es una biblioteca de Python para el manejo de matrices, arreglos, manipulación matemática, lógica y mucho más.
- `matplotlib`: es una biblioteca para crear visualizaciones estáticas, animadas e interactivas en Python.

Para poder modelar el juego de la vida usando el framework de `mesa` es necesario importar dos clases: una para el modelo general, y otro para los agentes. 

In [1]:
!pip install mesa
# La clase `Model` se hace cargo de los atributos a nivel del modelo, maneja los agentes. 
# Cada modelo puede contener múltiples agentes y todos ellos son instancias de la clase `Agent`.
from mesa import Agent, Model 

# Debido a que necesitamos un solo agente por celda elegimos `SingleGrid` que fuerza un solo objeto por celda.
from mesa.space import MultiGrid

# Con `SimultaneousActivation` hacemos que todos los agentes se activen de manera simultanea.
from mesa.time import SimultaneousActivation

# Vamos a hacer uso de `DataCollector` para obtener el grid completo cada paso (o generación) y lo usaremos para graficarlo.
from mesa.datacollection import DataCollector

# mathplotlib lo usamos para graficar/visualizar como evoluciona el autómata celular.
%matplotlib inline
import matplotlib
import matplotlib.pyplot as plt
import matplotlib.animation as animation
plt.rcParams["animation.html"] = "jshtml"
matplotlib.rcParams['animation.embed_limit'] = 2**128

# Definimos los siguientes paquetes para manejar valores númericos.
import numpy as np
import pandas as pd

# Definimos otros paquetes que vamos a usar para medir el tiempo de ejecución de nuestro algoritmo.
import time
import datetime
import random

     |████████████████████████████████| 668 kB 3.5 MB/s 
     |████████████████████████████████| 63 kB 1.1 MB/s 


## Crear el modelo

Antes que nada el presente modelo se encuentra basado en el [tutorial introductorio](https://mesa.readthedocs.io/en/master/tutorials/intro_tutorial.html). Lo modifiqué un poco para que funcionara para el presente problema pero en esencia es lo mismo.

In [19]:
def get_grid(model):
    '''
    Descripción
    '''
    grid = np.zeros((model.grid.width, model.grid.height))
    for cell in model.grid.coord_iter():
        cell_content, x, y = cell
        for obj in cell_content :
          if isinstance(obj, Vacuum) : 
            grid[x][y] = 2
          elif isinstance(obj, Cell) : 
            grid[x][y] = obj.estado
    return grid


In [24]:
class Vacuum(Agent) : 
  '''
  Nuestro agente que aspira el piso sucio
  '''
  def __init__(self, unique_id, model) : 
    super().__init__(unique_id, model)
    self.sig_pos = None

  def step(self) :
    vecinos = self.model.grid.get_neighbors(
      self.pos,
      moore=True,
      include_center=True)
    
    # maquina de estados
    for vecino in vecinos : 
      if isinstance(vecino, Cell) and self.pos == vecino.pos: 
        if vecino.estado == 1 : 
          # limpiar
          vecino.sig_estado = 0
          self.sig_pos = self.pos
        else : # ya está limpio
          # elegir posicion a movernos
          vecinos_2 = self.model.grid.get_neighborhood(
            self.pos,
            moore=True,
            include_center=False)
          vecino.sig_estado = 0
          self.sig_pos = self.random.choice(vecinos_2)
        break
  
  def advance(self) : 
    vecinos = self.model.grid.get_neighbors(
      self.pos,
      moore=True,
      include_center=True)
    
    for vecino in vecinos : 
      if(isinstance(vecino, Cell)) and self.pos == vecino.pos:
        vecino.estado = vecino.sig_estado
        break
    self.model.grid.move_agent(self, self.sig_pos)

In [21]:
class Cell(Agent) : 
  '''
  Nuestro agente que representa una celda
  '''
  def __init__(self, unique_id, model, estado) : 
    super().__init__(unique_id, model)
    self.pos = unique_id
    self.sig_estado = None
    self.estado = estado # 0, si es limpio o 1 si es sucio

In [22]:
class Habitacion(Model) : 
  '''
  Nuestro Modelo
  '''
  def __init__(self, M, N, num_agentes, porc_celdas_sucias) : 
    self.num_agentes = num_agentes
    self.porc_celdas_sucias = porc_celdas_sucias
    self.porc_celdas_limpias = 1 - porc_celdas_sucias
    self.grid = MultiGrid(M, N, False)
    self.schedule = SimultaneousActivation(self)
    

    # Celdas limpias/sucias
    num_celdas_sucias = int(M * N * porc_celdas_sucias)
    for (content, x, y) in self.grid.coord_iter():
      num = random.randint(0,1)
      # Poner las celdas sucias
      if num == 1 and num_celdas_sucias > 0: # NO siempre se va a cumplir, hay que revisarlo
        a = Cell((x, y), self, 1)
        num_celdas_sucias -= 1
      else :
        a = Cell((x, y), self, 0)
      self.grid.place_agent(a, (x,y))
      self.schedule.add(a)
    
    # Vacuum agent
    for id in range(num_agentes) : 
      v = Vacuum(id, self)
      self.grid.place_agent(v, (1,1))
      self.schedule.add(v)
    
    self.datacollector = DataCollector(model_reporters={"Grid": get_grid})

  def step(self) :
    self.datacollector.collect(self)
    self.schedule.step()

  def is_clean(self):
    for (content, x, y) in self.grid.coord_iter():
      for obj in content:
        if isinstance(obj, Cell) and obj.estado == 1:
          return False
    return True

A continuación corremos el modelo

In [31]:
# Definimos el tamaño del Grid
M = 20
N = 20
num_agentes = 5
porc_celdas_sucias = 0.4
tiempo_ejecucion = 1

# Registramos el tiempo de inicio y corremos el modelo
start_time = time.time()
model = Habitacion(M, N, num_agentes, porc_celdas_sucias) # Params: M, N, num_agentes, porcentaje_celdas
while ((time.time() - start_time) < tiempo_ejecucion) and not model.is_clean(): # que pasa si ya se limpio todo y aun tenemos tiempo
    model.step()

# Imprimimos el tiempo que le tomó correr al modelo.
print('Tiempo de ejecución:', str(datetime.timedelta(seconds=(time.time() - start_time))))



Tiempo de ejecución: 0:00:01.000318


In [32]:
all_grid = model.datacollector.get_model_vars_dataframe()
print(all_grid.to_string())

Obtenemos la información que almacenó el colector, este nos entregará un DataFrame de pandas que contiene toda la información.

In [33]:
all_grid = model.datacollector.get_model_vars_dataframe()

Graficamos la información usando `matplotlib`

In [34]:
%%capture

fig, axs = plt.subplots(figsize=(7,7))
axs.set_xticks([])
axs.set_yticks([])
patch = plt.imshow(all_grid.iloc[0][0], cmap=plt.cm.binary)

def animate(i):
    patch.set_data(all_grid.iloc[i][0])
    
anim = animation.FuncAnimation(fig, animate, frames=len(all_grid))

In [35]:
anim